# Exporting Features
This notebook contains the class definition for `Feature` objects, i.e. 1-dimensionnal pandas dataframes storing the value of a particular feature for every gap. It allows easier manipulation and export to - or import from - .csv files.

In [1]:
import pandas as pd
import geopandas as gpd
import numpy as np
import geopy.distance
from shapely.geometry import Point
from scipy.spatial import KDTree
from features import Feature
from utils import getValues, DATASETS_DIRECTORY_PATH

In [2]:
dynamic = pd.read_csv(f'{DATASETS_DIRECTORY_PATH}dynamic.csv', parse_dates=['timestamp'])
dynamic['geometry'] = gpd.GeoSeries.from_wkt(dynamic['geometry'], crs='EPSG:4326')
dynamic = gpd.GeoDataFrame(dynamic)

gaps = pd.read_csv(f'{DATASETS_DIRECTORY_PATH}gaps.csv', parse_dates=['disappeartime', 'reappeartime'])
gaps['geometry'] = gpd.GeoSeries.from_wkt(gaps['geometry'], crs='EPSG:4326')
gaps = gpd.GeoDataFrame(gaps, geometry=gaps.geometry, crs='EPSG:4326')
gaps['disappearlocation'] = gpd.GeoSeries.from_wkt(gaps['disappearlocation'], crs='EPSG:4326')
gaps['reappearlocation'] = gpd.GeoSeries.from_wkt(gaps['reappearlocation'], crs='EPSG:4326')

edges = pd.read_csv(f'{DATASETS_DIRECTORY_PATH}edges.csv')
edges['geometry'] = gpd.GeoSeries.from_wkt(edges['geometry'], crs='EPSG:4326')
edges = gpd.GeoDataFrame(edges, geometry=edges.geometry, crs='EPSG:4326')

In [3]:
Feature('darkspeed', gaps.darkspeed).save()
Feature('darkduration', gaps.darkduration).save()

In [4]:
def getBearing(A, B):
        lonA, latA, lonB, latB = A.x, A.y, B.x, B.y
        lonA, latA, lonB, latB = np.radians(lonA), np.radians(latA), np.radians(lonB), np.radians(latB)
        temp1 = np.sin(lonB - lonA)*np.cos(latB)
        temp2 = np.cos(latA)*np.sin(latB) - np.sin(latA)*np.cos(latB)*np.cos(lonB - lonA)
        return (np.degrees(np.arctan2(temp1, temp2)) + 360) % 360

def deviationFromCourse(gap):
    bearing = getBearing(gap.disappearlocation, gap.reappearlocation)
    course = dynamic.loc[gap.disappearid].courseoverground
    return np.round(np.min((abs(bearing - course), (360 - abs(bearing - course)))), 1)

deviation = gaps.apply(deviationFromCourse, axis=1)
Feature('deviationSin', deviation.apply(lambda x: np.sin(np.radians(x)))).save()
Feature('deviationCos', deviation.apply(lambda x: np.cos(np.radians(x)))).save()

In [5]:
antennaLocation = Point(-4.570077, 48.358767)

def bearingFromAntenna(point):
    return getBearing(antennaLocation, point)

def gpd2geopy(point):
    return geopy.distance.lonlat(point.x, point.y)

def distanceFromAntenna(point):
    return geopy.distance.geodesic(gpd2geopy(antennaLocation), gpd2geopy(point)).nm

disappearBearing = gaps.disappearlocation.apply(bearingFromAntenna)
reappearBearing = gaps.reappearlocation.apply(bearingFromAntenna)
disappearDistance = gaps.disappearlocation.apply(distanceFromAntenna)
reappearDistance = gaps.reappearlocation.apply(distanceFromAntenna)

Feature('disappearBearingSin', disappearBearing.apply(lambda x: np.sin(np.radians(x)))).save()
Feature('disappearBearingCos', disappearBearing.apply(lambda x: np.cos(np.radians(x)))).save()

Feature('reappearBearingSin', reappearBearing.apply(lambda x: np.sin(np.radians(x)))).save()
Feature('reappearBearingCos', reappearBearing.apply(lambda x: np.cos(np.radians(x)))).save()

Feature('disappearDistance', disappearDistance).save()
Feature('reappearDistance', reappearDistance).save()

Before using the `KDTree` from `scipy.spatial`, it is useful to verify that the index of the concerned dataframe (here `dynamic`) is equal to the natural integer index (i.e. the integer sequence starting at 0 with a step of 1). This allows to use interchangeably pandas `.loc` and `.iloc` methods, and avoids any problems whenever working with a numpy `array` representation of a dataframe.

In [6]:
dynamic.index.equals(dynamic.reset_index(drop=True).index)

True

In [7]:
%%time
tree = KDTree(np.array([dynamic.geometry.x, dynamic.geometry.y]).T)
neighbours = 20

def localEdgeRatio(dynamic_id, neighbours=neighbours):
    coordinates = np.array([dynamic.loc[dynamic_id].geometry.x, dynamic.loc[dynamic_id].geometry.y]).T
    distances, neighboursIds = tree.query(coordinates, neighbours + 1)
    distances, neighboursIds = distances[1:], neighboursIds[1:]
    distances = np.maximum(distances, 1e-4) #avoids dividing by 0 when computing weights
    weights = np.min(distances) / distances
    isEdge = np.array([not (dynamic.loc[neighbourId].edge == 'none') for neighbourId in neighboursIds]).astype(int)
    return np.sum(isEdge * weights) / np.sum(weights)

disappearEdgeRatio = gaps.disappearid.apply(localEdgeRatio)
reappearEdgeRatio = gaps.reappearid.apply(localEdgeRatio)

Feature('disappearEdgeRatio', disappearEdgeRatio).save()
Feature('reappearEdgeRatio', reappearEdgeRatio).save()

CPU times: total: 33.2 s
Wall time: 45.9 s


> NB : using the `KDTree` implementation from `scipy.spatial` entails significant gains in terms of computation time, but it relies on the euclidean norm in the 2d-space of (longitude, latitude). This creates a bias since degrees of latitude are not all equals to the same geodesic distance, but this bias is considered acceptable with regard to the aforementioned gains in performance.

In [8]:
gaps['disappearEdgeRatio'] = disappearEdgeRatio
gaps[['disappearlocation', 'disappearEdgeRatio']].set_geometry('disappearlocation').explore(column='disappearEdgeRatio')